# Twitter Video Game Analytics

In [9]:
from geopy.geocoders import Nominatim
from requests_oauthlib import OAuth1
from pandas.io.json import json_normalize
import matplotlib.pyplot as plt
import us
import tweepy
import json
import re
import geocoder
import pandas as pd
import numpy as np
import fiona

In [3]:
file = '../twitter.xlsx'
data = list(pd.read_excel(file,header=1))
access_token = str(data[0])
access_token_secret = str(data[1])
consumer_key = str(data[2])
consumer_secret = str(data[3])
google = str(data[4])

In [4]:
auth = tweepy.OAuthHandler(consumer_key, consumer_secret)
auth.set_access_token(access_token,access_token_secret)
api = tweepy.API(auth)
search_text = ["%23Battlefield1","%23BF1"]

In [5]:
search_results = []
for status in tweepy.Cursor(api.search, q=search_text,lang='en',retweeted_status=False).items(2000):
    search_results.append(status._json)   
with open('search_results.json', 'w') as file:
    json.dump(search_results,file)
print search_results

[{u'contributors': None, u'truncated': True, u'text': u'It\u2019s ok @Battlefield I no longer wanted to watch the battlepack unboxing  animations since the recent update!\u2026 https://t.co/hZ5n32IwbN', u'is_quote_status': False, u'in_reply_to_status_id': None, u'id': 960958785127886848, u'favorite_count': 0, u'entities': {u'symbols': [], u'user_mentions': [{u'id': 27855118, u'indices': [8, 20], u'id_str': u'27855118', u'screen_name': u'Battlefield', u'name': u'Battlefield'}], u'hashtags': [], u'urls': [{u'url': u'https://t.co/hZ5n32IwbN', u'indices': [111, 134], u'expanded_url': u'https://twitter.com/i/web/status/960958785127886848', u'display_url': u'twitter.com/i/web/status/9\u2026'}]}, u'retweeted': False, u'coordinates': None, u'source': u'<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>', u'in_reply_to_screen_name': None, u'in_reply_to_user_id': None, u'retweet_count': 0, u'id_str': u'960958785127886848', u'favorited': False, u'user': {u'follow_r

In [6]:
def byteify(input):
    if isinstance(input, dict):
        return {byteify(key): byteify(value)
                for key, value in input.iteritems()}
    elif isinstance(input, list):
        return [byteify(element) for element in input]
    elif isinstance(input, unicode):
        return input.encode('utf-8')
    else:
        return input

In [10]:
json_df = json.load((open('search_results.json')),object_hook=byteify)
json_df = json_normalize(json_df)
print json_df.head()
json_df = json_df.dropna(how='all',axis=1)
print json_df.columns
json_df = json_df[json_df['user.location'] != '']

  contributors  coordinates coordinates.coordinates coordinates.type  \
0         None          NaN                     NaN              NaN   
1         None          NaN                     NaN              NaN   
2         None          NaN                     NaN              NaN   
3         None          NaN                     NaN              NaN   
4         None          NaN                     NaN              NaN   

                       created_at  \
0  Tue Feb 06 19:30:02 +0000 2018   
1  Tue Feb 06 18:36:32 +0000 2018   
2  Tue Feb 06 18:33:59 +0000 2018   
3  Tue Feb 06 17:21:00 +0000 2018   
4  Tue Feb 06 17:19:06 +0000 2018   

                                   entities.hashtags  \
0                                                 []   
1  [{u'indices': [41, 54], u'text': u'Battlefield...   
2  [{u'indices': [41, 54], u'text': u'Battlefield...   
3  [{u'indices': [72, 76], u'text': u'BF1'}, {u'i...   
4  [{u'indices': [72, 76], u'text': u'BF1'}, {u'i...   

       

In [11]:
print json_df['user.location']

0                                York
3             England, United Kingdom
4                     Los Angeles, CA
6                 Original RT Account
7                      San Antonio TX
9                Somewhere in France 
10                    #WaveformGaming
11                            Ireland
16                    #WaveformGaming
17                    #WaveformGaming
18                   Augsburg, Bayern
19                    @WaveformGaming
20                            Germany
24         ( Instagram : LegendHadi )
27         ( Instagram : LegendHadi )
28         ( Instagram : LegendHadi )
29                Bayern, Deutschland
30     On a 722 & BFFS GAMING server!
31                    #WaveformGaming
32              Western Europe - 🇳🇱
33                        Deutschland
34                    #WaveformGaming
35                            Ireland
36       Stratford-Upon-Avon, England
37                 Stockholm / Sweden
38            England, United Kingdom
39           S

In [12]:
def match_boolean(text):
    if not text:
        return False
    else:
        print text
        if re.search(r"\s*[,]\s*", str(text)):
            text = text.split(', ')
        elif re.search('(?<=-)\w+', str(text)):
            text = text.split('-')
        return True 

In [13]:
us_comments = pd.DataFrame()
appended_data = {}
for each in json_df['user.location']:
    match = match_boolean(each)
    if match:
        appended_data[each] = json_df[json_df['user.location'] == each]
us_comments = appended_data
print us_comments
for each in us_comments:
    print each
    print us_comments[each]['user.location']

York
England, United Kingdom
Los Angeles, CA
Original RT Account
San Antonio TX
Somewhere in France 
#WaveformGaming
Ireland
#WaveformGaming
#WaveformGaming
Augsburg, Bayern
@WaveformGaming
Germany
( Instagram : LegendHadi )
( Instagram : LegendHadi )
( Instagram : LegendHadi )
Bayern, Deutschland
On a 722 & BFFS GAMING server!
#WaveformGaming
Western Europe - 🇳🇱
Deutschland
#WaveformGaming
Ireland
Stratford-Upon-Avon, England
Stockholm / Sweden
England, United Kingdom
Scotland, United Kingdom
#WaveformGaming
Christmas Island
Россия
madrid
PDX
#WaveformGaming
#WaveformGaming
United States
United States
United States
vienna
USA
#WaveformGaming
Scotland, United Kingdom
Battlefield, owner: Rowniss
PS4
United States
Warren County, MO
Worldwide
San Antonio TX
Bayern, Deutschland
Vault 111
#WaveformGaming
@DNR_CREW - @DNRCREWNETWORK
Italy
United Kingdom
New York, USA
Illinois, USA
#WaveformGaming
Original RT Account
Stockport, England
England, United Kingdom
Italy
Ireland
Italy
Bayern, Deuts

UK
Germany
Москва, Россия
Larne, Northern Ireland
#WaveformGaming
Red light district
Barcelona, España
Edinburgh, Scotland
( Instagram : LegendHadi )
( Instagram : LegendHadi )
( Instagram : LegendHadi )
St-Louis France Swiss Germany
#WaveformGaming
#WaveformGaming
@WaveformGaming
 USA
Germany
Sligo, Ireland
east sussex england
Under ur fucking bed! NOW PTFO
Pennsylvania, USA
Oklahoma, USA
South East, England
#WaveformGaming
Stockport, England
Seattle, WA
#WaveformGaming
#WaveformGaming
@WaveformGaming
Ohio, USA
TheDen
Original RT Account
Stockport, England
United States
United States
Belfast, Ireland
Deutschland
Manchester, England
Seattle, WA
#WaveformGaming
#WaveformGaming
@WaveformGaming
Stockport, England
Stockport, England
Belfast, Ireland
#WaveformGaming
#WaveformGaming
@WaveformGaming
Germany
South East, England
Cork
United States
United States
England, United Kingdom
United States
United States
United States
Monticello, NY
St-Louis France Swiss Germany
United States
#WaveformG

375    Game World
Name: user.location, dtype: object
MidWest
179    MidWest
Name: user.location, dtype: object
South East, England
134    South East, England
135    South East, England
171    South East, England
178    South East, England
207    South East, England
225    South East, England
275    South East, England
345    South East, England
393    South East, England
437    South East, England
438    South East, England
564    South East, England
581    South East, England
610    South East, England
611    South East, England
701    South East, England
739    South East, England
Name: user.location, dtype: object
USA // United Kingdom
587    USA // United Kingdom
Name: user.location, dtype: object
( Instagram : LegendHadi )
24     ( Instagram : LegendHadi )
27     ( Instagram : LegendHadi )
28     ( Instagram : LegendHadi )
210    ( Instagram : LegendHadi )
236    ( Instagram : LegendHadi )
237    ( Instagram : LegendHadi )
308    ( Instagram : LegendHadi )
380    ( Instagram : Leg

Poços de Caldas, Brasil
110    Poços de Caldas, Brasil
Name: user.location, dtype: object
Bruxelles, Belgique  🇧🇪🇵🇹
462    Bruxelles, Belgique  🇧🇪🇵🇹
Name: user.location, dtype: object
Barcelona, España
240    Barcelona, España
514    Barcelona, España
682    Barcelona, España
Name: user.location, dtype: object
Bayern, Deutschland
29    Bayern, Deutschland
68    Bayern, Deutschland
86    Bayern, Deutschland
Name: user.location, dtype: object
Syria
427    Syria
Name: user.location, dtype: object
Tifton, GA
346    Tifton, GA
Name: user.location, dtype: object
Bolzano, Italy
562    Bolzano, Italy
Name: user.location, dtype: object
Illinois, USA
76    Illinois, USA
Name: user.location, dtype: object
Monheim am Rhein, Deutschland
552    Monheim am Rhein, Deutschland
Name: user.location, dtype: object
Greenock, Scotland
446    Greenock, Scotland
Name: user.location, dtype: object
Belgrade
405    Belgrade
Name: user.location, dtype: object
Riyadh
472    Riyadh
Name: user.location, dtype: objec

In [14]:
temp_coords = []
for each in us_comments:
    geo = geocoder.google(each,key=google)
    temp_coords.append([geo.city, geo.state, geo.country,geo.lat, geo.lng])
print temp_coords

[[None, None, u'CA', 56.130366, -106.346771], [u'Oklahoma City', u'OK', u'US', 35.5455951, -97.5652454], [None, u'MS', u'US', 32.3546679, -89.3985283], [u'Leduc', u'AB', u'CA', 53.2580126, -113.5502218], [u'Jeff', u'IN', u'US', 38.2775702, -85.7371847], [u'South Shields', u'England', u'GB', 54.999424, -1.427406], [u'Mumbai', u'MH', u'IN', 19.137839, 72.832196], [None, u'IN', u'US', 40.2671941, -86.1349019], [u'Exeter', u'England', u'GB', 50.718412, -3.533899], [u'South Coffeyville', u'OK', u'US', 36.949343, -95.644246], [None, u'TX', u'US', 31.9685988, -99.9018131], [u'San Antonio', u'TX', u'US', 29.4241219, -98.49362819999999], [None, u'England', u'GB', 52.4750743, -1.829833], [None, u'Scotland', u'GB', 56.49067119999999, -4.2026458], [u'Las Palmas de Gran Canaria', u'CN', u'ES', 28.1235459, -15.4362574], [None, None, None, None, None], [u'Amsterdam', u'NH', u'NL', 52.3718604, 4.895861000000001], [None, None, None, None, None], [None, u'TN', u'US', 35.5174913, -86.5804473], [u'Washing

In [15]:
clean_df = pd.DataFrame(data=temp_coords, columns=['city','state','country','lat','lng'])


In [16]:
print clean_df.head()


            city state country        lat         lng
0           None  None      CA  56.130366 -106.346771
1  Oklahoma City    OK      US  35.545595  -97.565245
2           None    MS      US  32.354668  -89.398528
3          Leduc    AB      CA  53.258013 -113.550222
4           Jeff    IN      US  38.277570  -85.737185


In [ ]:
clean_df.state.value_counts(dropna=True)

England                            18
TX                                  7
OK                                  6
MO                                  5
Scotland                            4
Riyadh Province                     4
NY                                  4
IN                                  4
CA                                  4
IL                                  4
OH                                  3
NSW                                 3
Northern Ireland                    3
Stockholm County                    3
Normandy                            2
NC                                  2
Community of Madrid                 2
CN                                  2
CO                                  2
TN                                  2
WA                                  2
NRW                                 2
BY                                  2
FL                                  2
MS                                  2
GA                                  2
NH          

In [ ]:
from mpl_toolkits.basemap import Basemap
lat = [a for a in clean_df['lat']] 
lng = [b for b in clean_df['lng']]
fig = plt.figure(figsize=(10,10))
earth = Basemap(projection = 'merc', llcrnrlat =-80, urcrnrlat = 80, \
            llcrnrlon = -180, urcrnrlon = 180, lat_ts = 20, \
            resolution = 'c')
x,y = earth(lng,lat)
earth.drawcoastlines(color='0.50', linewidth=0.25)
earth.fillcontinents(color='0.95')
plt.scatter(x,y,10, marker='o',color='Red')
plt.show()